# Footfall Visualizations

## Problem Statement
To visualize footfall queried from DataSpark's DAAS(Data-As-A-Service) API.

## Input parameters

In [1]:
%matplotlib inline

import base64
import folium
import geopandas as gpd
import json
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import requests

from pandas.io.json import json_normalize

#### Input parameters #####################################
consumerKey = "7U0FUKqQfcBlV4RaT6OqtRRiRcga"
consumerSecret = "C9fiGvQAksiYN16EQDQtVBIPEgUa"
startDate = '2017-01-11'
startTime = '00:00:00'
endDate = '2017-01-11'
endTime = '23:59:59'
interval = 'day'
###########################################################

filename_pr_in = "./data/planning-region-id.geojson"
filename_pa_in = "./data/planning-area-id.geojson"
filename_sz_in = "./data/sub-zone-id.geojson"
figsizeParams = (12, 8)
urlAccessTok = 'https://apistore.datasparkanalytics.com/token'
urlFootfall = 'https://apistore.datasparkanalytics.com/footfall/v2/all/present'

## Common functions

In [2]:
# Fire query and return the response
def getResponse(url, payload, headers):
    try:
        return requests.post(url, data = payload, headers = headers)
    except requests.exceptions.RequestException as e:
        return "Error: {}".format(e)

# Fire a query to get access token and return the access token
def getAccessToken(url, consumerKey, consumerSecret):
    keySecret = (consumerKey + ":" + consumerSecret).encode('utf-8')
    encoded = base64.b64encode(keySecret).decode('utf-8')

    headers = {
        'Authorization': 'Basic ' + encoded, 
    }

    payload = {
        'grant_type': 'client_credentials'
    }

    r = getResponse(url, payload, headers)
    print 'r = ' + str(r)
    print 'r.text = ' + str(r.text)

    try: 
        r.json()['access_token']
    except KeyError:
        print "Error: unable to get access token. Make sure you keyed in you consumerKey and consumerSecret correctly." 	
        sys.exit(0)

    return r.json()['access_token']

## Get access token

In [3]:
startDateTime = startDate + 'T' + startTime + 'Z'
endDateTime = endDate + 'T' + endTime + 'Z'

accessToken = getAccessToken(urlAccessTok, consumerKey, consumerSecret)
print 'accessToken = ' + str(accessToken)

headers = {
    'Authorization': 'Bearer ' + accessToken, 
    'Content-Type': 'application/json'
}


r = <Response [200]>
r.text = {"access_token":"dccba40b-f406-31fa-bbf2-e865e7b15f50","scope":"am_application_scope default","token_type":"Bearer","expires_in":86400}
accessToken = dccba40b-f406-31fa-bbf2-e865e7b15f50


## Query the API and get response for planning-region

In [4]:
payload = {
    "startDateTime": startDateTime,
    "endDateTime": endDateTime,
    "roiLayer": 'planning-region',
    "interval": interval
}
r = getResponse(urlFootfall, json.dumps(payload), headers)
# print "r = " + str(r)
# print "r.text = " + str(r.text)
r_json = r.json()
results_pr = json_normalize(r_json['results'])
results_pr

interval roiId     values
0      day     1  [2512379]
1      day     5  [1476472]
2      day     4  [1348002]
3      day     2  [1141512]
4      day     3  [1015664]
5    total     1  [2512379]
6    total     5  [1476472]
7    total     4  [1348002]
8    total     2  [1141512]
9    total     3  [1015664]

## Query the API and get response for planning-area

In [5]:
payload = {
    "startDateTime": startDateTime,
    "endDateTime": endDateTime,
    "roiLayer": 'planning-area',
    "interval": interval
}
r = getResponse(urlFootfall, json.dumps(payload), headers)
# print "r = " + str(r)
# print "r.text = " + str(r.text)
r_json = r.json()
results_pa = json_normalize(r_json['results'])
results_pa

interval roiId    values
0        day    22  [733139]
1        day    53  [614765]
2        day    31  [709072]
3        day     8  [783383]
4        day    46  [722565]
5        day    16  [809450]
6        day    49  [595572]
7        day    35  [534533]
8        day    50  [900032]
9        day    26  [657045]
10       day    38  [602783]
11       day    30  [487483]
12       day    39  [575704]
13       day    28  [794681]
14       day    24  [418914]
15       day     7  [453618]
16       day    25  [579240]
17       day    17  [669629]
18       day    10  [542848]
19       day    14  [350424]
20       day    15  [487780]
21       day    58  [471735]
22       day    21  [299473]
23       day    18  [329039]
24       day     6  [505695]
25       day     9  [356989]
26       day    48  [221713]
27       day    12  [274545]
28       day    34  [372598]
29       day    56  [449046]
..       ...   ...       ...
80     total     9  [356989]
81     total    48  [221713]
82     total    12  [274545]
83     total    34  [372598]
84     total    56  [449046]
85     total    45  [280168]
86     total    55  [410822]
87     total    42  [286870]
88     total    44  [229358]
89     total    52  [257863]
90     total    23  [221452]
91     total    54   [96691]
92     total    29  [165314]
93     total    59  [303986]
94     total    33  [282517]
95     total    37  [284766]
96     total    57  [139922]
97     total    20  [178063]
98     total    19  [189904]
99     total    47   [85145]
100    total    11  [187126]
101    total    32  [199378]
102    total    60   [97326]
103    total    36  [172467]
104    total    40   [59722]
105    total    41   [88213]
106    total    43   [18470]
107    total    51   [11821]
108    total    27   [20633]
109    total    13    [6925]

[110 rows x 3 columns]

## Query the API and get response for sub-zone

In [6]:
payload = {
    "startDateTime": startDateTime,
    "endDateTime": endDateTime,
    "roiLayer": 'sub-zone',
    "interval": interval
}
r = getResponse(urlFootfall, json.dumps(payload), headers)
# print "r = " + str(r)
# print "r.text = " + str(r.text)
r_json = r.json()
results_sz = json_normalize(r_json['results'])
results_sz

interval roiId    values
0        day   249  [313784]
1        day   223  [464174]
2        day   259  [284438]
3        day   329  [227133]
4        day   274  [319815]
5        day   350  [245863]
6        day   242  [208390]
7        day   197  [336109]
8        day   230  [318323]
9        day   253  [240132]
10       day   170  [329374]
11       day    98  [289579]
12       day   212  [232614]
13       day   332  [225811]
14       day   209  [232356]
15       day   241  [392122]
16       day   169  [397257]
17       day   227  [215094]
18       day   225  [337250]
19       day    76   [96691]
20       day   273  [249953]
21       day   250  [240661]
22       day   347  [192901]
23       day   345  [165314]
24       day   240  [261324]
25       day   143  [219643]
26       day   177  [222832]
27       day   291  [208796]
28       day   168  [195203]
29       day   260  [250913]
..       ...   ...       ...
588    total    93   [42863]
589    total    70   [37547]
590    total   130   [33551]
591    total   120   [31811]
592    total   115   [13957]
593    total   382   [11142]
594    total   136   [73599]
595    total   147   [36571]
596    total   166   [32227]
597    total   258   [13100]
598    total   353   [13108]
599    total   151   [13417]
600    total   205   [44293]
601    total   312   [20633]
602    total   316   [20599]
603    total   222   [32953]
604    total   378   [20206]
605    total    79   [12583]
606    total   294    [6925]
607    total   269   [23404]
608    total   307   [10245]
609    total   304    [4278]
610    total   251   [14636]
611    total   321   [10909]
612    total   338    [1551]
613    total   187    [1439]
614    total   144    [1073]
615    total   198    [1910]
616    total   159     [565]
617    total   204     [200]

[618 rows x 3 columns]

## Extract the total footfall for that day for planning-region

In [7]:
results_pr = results_pr[results_pr['interval'] == 'total'].reset_index()
results_pr['roiId'] = results_pr['roiId'].apply(lambda x: int(x))
results_pr['values'] = results_pr['values'].apply(lambda x: int(x[0]))
print results_pr['values'].sum()
results_pr


7494029


index interval  roiId   values
0      5    total      1  2512379
1      6    total      5  1476472
2      7    total      4  1348002
3      8    total      2  1141512
4      9    total      3  1015664

## Extract the total footfall for that day for planning-area

In [8]:
results_pa = results_pa[results_pa['interval'] == 'total'].reset_index()
results_pa['roiId'] = results_pa['roiId'].apply(lambda x: int(x))
results_pa['values'] = results_pa['values'].apply(lambda x: int(x[0]))
results_pa

index interval  roiId  values
0      55    total     22  733139
1      56    total     53  614765
2      57    total     31  709072
3      58    total      8  783383
4      59    total     46  722565
5      60    total     16  809450
6      61    total     49  595572
7      62    total     35  534533
8      63    total     50  900032
9      64    total     26  657045
10     65    total     38  602783
11     66    total     30  487483
12     67    total     39  575704
13     68    total     28  794681
14     69    total     24  418914
15     70    total      7  453618
16     71    total     25  579240
17     72    total     17  669629
18     73    total     10  542848
19     74    total     14  350424
20     75    total     15  487780
21     76    total     58  471735
22     77    total     21  299473
23     78    total     18  329039
24     79    total      6  505695
25     80    total      9  356989
26     81    total     48  221713
27     82    total     12  274545
28     83    total     34  372598
29     84    total     56  449046
30     85    total     45  280168
31     86    total     55  410822
32     87    total     42  286870
33     88    total     44  229358
34     89    total     52  257863
35     90    total     23  221452
36     91    total     54   96691
37     92    total     29  165314
38     93    total     59  303986
39     94    total     33  282517
40     95    total     37  284766
41     96    total     57  139922
42     97    total     20  178063
43     98    total     19  189904
44     99    total     47   85145
45    100    total     11  187126
46    101    total     32  199378
47    102    total     60   97326
48    103    total     36  172467
49    104    total     40   59722
50    105    total     41   88213
51    106    total     43   18470
52    107    total     51   11821
53    108    total     27   20633
54    109    total     13    6925

## Extract the total footfall for that day for sub-zone

In [9]:
results_sz = results_sz[results_sz['interval'] == 'total'].reset_index()
results_sz['roiId'] = results_sz['roiId'].apply(lambda x: int(x))
results_sz['values'] = results_sz['values'].apply(lambda x: int(x[0]))
results_sz

index interval  roiId  values
0      309    total    249  313784
1      310    total    223  464174
2      311    total    259  284438
3      312    total    329  227133
4      313    total    274  319815
5      314    total    350  245863
6      315    total    242  208390
7      316    total    197  336109
8      317    total    230  318323
9      318    total    253  240132
10     319    total    170  329374
11     320    total     98  289579
12     321    total    212  232614
13     322    total    332  225811
14     323    total    209  232356
15     324    total    241  392122
16     325    total    169  397257
17     326    total    227  215094
18     327    total    225  337250
19     328    total     76   96691
20     329    total    273  249953
21     330    total    250  240661
22     331    total    347  192901
23     332    total    345  165314
24     333    total    240  261324
25     334    total    143  219643
26     335    total    177  222832
27     336    total    291  208796
28     337    total    168  195203
29     338    total    260  250913
..     ...      ...    ...     ...
279    588    total     93   42863
280    589    total     70   37547
281    590    total    130   33551
282    591    total    120   31811
283    592    total    115   13957
284    593    total    382   11142
285    594    total    136   73599
286    595    total    147   36571
287    596    total    166   32227
288    597    total    258   13100
289    598    total    353   13108
290    599    total    151   13417
291    600    total    205   44293
292    601    total    312   20633
293    602    total    316   20599
294    603    total    222   32953
295    604    total    378   20206
296    605    total     79   12583
297    606    total    294    6925
298    607    total    269   23404
299    608    total    307   10245
300    609    total    304    4278
301    610    total    251   14636
302    611    total    321   10909
303    612    total    338    1551
304    613    total    187    1439
305    614    total    144    1073
306    615    total    198    1910
307    616    total    159     565
308    617    total    204     200

[309 rows x 4 columns]

## Add the missing subzones into dataframe

In [10]:
temp = pd.DataFrame({'interval': ['total'] * 14, 
                     'roiId':[77, 78, 104, 107, 110, 243, 263, 334, 346, 355, 361, 364, 372, 379], 
                     'values':[0] * 14})
results_sz = pd.concat([results_sz, temp])
results_sz

index interval  roiId  values
0    309.0    total    249  313784
1    310.0    total    223  464174
2    311.0    total    259  284438
3    312.0    total    329  227133
4    313.0    total    274  319815
5    314.0    total    350  245863
6    315.0    total    242  208390
7    316.0    total    197  336109
8    317.0    total    230  318323
9    318.0    total    253  240132
10   319.0    total    170  329374
11   320.0    total     98  289579
12   321.0    total    212  232614
13   322.0    total    332  225811
14   323.0    total    209  232356
15   324.0    total    241  392122
16   325.0    total    169  397257
17   326.0    total    227  215094
18   327.0    total    225  337250
19   328.0    total     76   96691
20   329.0    total    273  249953
21   330.0    total    250  240661
22   331.0    total    347  192901
23   332.0    total    345  165314
24   333.0    total    240  261324
25   334.0    total    143  219643
26   335.0    total    177  222832
27   336.0    total    291  208796
28   337.0    total    168  195203
29   338.0    total    260  250913
..     ...      ...    ...     ...
293  602.0    total    316   20599
294  603.0    total    222   32953
295  604.0    total    378   20206
296  605.0    total     79   12583
297  606.0    total    294    6925
298  607.0    total    269   23404
299  608.0    total    307   10245
300  609.0    total    304    4278
301  610.0    total    251   14636
302  611.0    total    321   10909
303  612.0    total    338    1551
304  613.0    total    187    1439
305  614.0    total    144    1073
306  615.0    total    198    1910
307  616.0    total    159     565
308  617.0    total    204     200
0      NaN    total     77       0
1      NaN    total     78       0
2      NaN    total    104       0
3      NaN    total    107       0
4      NaN    total    110       0
5      NaN    total    243       0
6      NaN    total    263       0
7      NaN    total    334       0
8      NaN    total    346       0
9      NaN    total    355       0
10     NaN    total    361       0
11     NaN    total    364       0
12     NaN    total    372       0
13     NaN    total    379       0

[323 rows x 4 columns]

## Plot choropleth for planning-region

In [11]:
geo_str = json.dumps(json.load(open(filename_pr_in, 'r')))
threshold_scale = np.linspace(results_pr['values'].min(), results_pr['values'].max(), 6, dtype=int).tolist()

map_osm = folium.Map(location=[1.28443, 103.85662], zoom_start=11)
map_osm.choropleth(geo_str=geo_str,
              data=results_pr,
              columns=['roiId', 'values'],
              fill_color='YlGn',
              key_on='feature.id',   
              threshold_scale=threshold_scale)
map_osm

## Plot choropleth for planning-area

In [12]:
geo_str = json.dumps(json.load(open(filename_pa_in, 'r')))
threshold_scale = np.linspace(results_pa['values'].min(), results_pa['values'].max(), 6, dtype=int).tolist()

map_osm = folium.Map(location=[1.28443, 103.85662], zoom_start=11)
map_osm.choropleth(geo_str=geo_str,
              data=results_pa,
              columns=['roiId', 'values'],
              fill_color='YlGn',
              key_on='feature.id',   
              threshold_scale=threshold_scale)
map_osm

## Plot choropleth for sub-zone

In [13]:
geo_str = json.dumps(json.load(open(filename_sz_in, 'r')))
threshold_scale = np.linspace(results_sz['values'].min(), results_sz['values'].max(), 6, dtype=int).tolist()

map_osm = folium.Map(location=[1.28443, 103.85662], zoom_start=11)
map_osm.choropleth(geo_str=geo_str,
              data=results_sz,
              columns=['roiId', 'values'],
              fill_color='YlGn',
              key_on='feature.id',   
              threshold_scale=threshold_scale)
map_osm